In [0]:
# IMPORTS
%matplotlib inline
from matplotlib import pyplot as plt
from tensorflow.keras.applications.resnet50 import preprocess_input
from tensorflow.keras.preprocessing.image import img_to_array
from tensorflow.keras.applications import ResNet50
from keras.models import Sequential
from keras.applications import InceptionResNetV2
from keras.layers import Dense, Dropout, Flatten, GlobalAveragePooling2D
from keras.optimizers import RMSprop, Adam, SGD

from IPython.display import clear_output
import numpy as np
import time
import json
import cv2
import os

Using TensorFlow backend.


In [0]:
!wget --no-check-certificate -r 'https://docs.google.com/uc?export=download&id=18744y_Oyqtx94kpuAeEbkdFGzg9p0_5M' -O dog-breed-identification.zip

!unzip dog-breed-identification.zip -d ./dataset
!unzip ./dataset/train.zip -d ./dataset
!unzip ./dataset/test.zip -d ./dataset
!rm -f ./dataset/train.zip
!rm -f ./dataset/test.zip

will be placed in the single file you specified.

--2019-11-16 19:13:37--  https://docs.google.com/uc?export=download&id=18744y_Oyqtx94kpuAeEbkdFGzg9p0_5M
Resolving docs.google.com (docs.google.com)... 74.125.23.101, 74.125.23.113, 74.125.23.139, ...
Connecting to docs.google.com (docs.google.com)|74.125.23.101|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘dog-breed-identification.zip’

dog-breed-identific     [ <=>                ]   3.19K  --.-KB/s    in 0s      

2019-11-16 19:13:37 (73.4 MB/s) - ‘dog-breed-identification.zip’ saved [3264]

Loading robots.txt; please ignore errors.
--2019-11-16 19:13:37--  https://docs.google.com/robots.txt
Reusing existing connection to docs.google.com:443.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/plain]
Saving to: ‘dog-breed-identification.zip’

dog-breed-identific     [ <=>                ]     567  --.-KB/s    in 0s      

2019-11-16 19:13:37 (143 MB/

# YOLO

### IoU for YOLO

In [0]:
def IoU(box1, box2):

    # Calculate the (y1, x1, y2, x2) coordinates of the intersection of box1 and box2. Calculate its Area.
    xi1 = max(box1[0], box2[0])
    yi1 = max(box1[1], box2[1])
    xi2 = min(box1[2], box2[2])
    yi2 = min(box1[3], box2[3])
    inter_area = (yi2 - yi1) * (xi2 - xi1)

    # Calculate the Union area by using Formula: Union(A,B) = A + B - Inter(A,B)
    box1_area = (box1[2] - box1[0]) * (box1[3] - box1[1])
    box2_area = (box2[2] - box2[0]) * (box2[3] - box2[1])
    union_area = box1_area + box2_area - inter_area

    # compute the IoU
    return inter_area / union_area

### YOLO with OpenCV

In [0]:
!wget --no-check-certificate -r 'https://docs.google.com/uc?export=download&id=1WZRUbjLDZRtV6_U6E-yxx8fskuIK3QO5' -O yolov3.weights
!wget --no-check-certificate -r 'https://docs.google.com/uc?export=download&id=1VLqx4cNeRGcefIEELDI9FR3P1gHj8Cap' -O yolov3.cfg
!wget "https://pjreddie.com/media/files/yolov3.weights" -O yolov33.weights

class YOLO:
    def __init__(self, CONFIDENCE= 0.4, THRESHOLD= 0.2):
        self.CONFIDENCE = CONFIDENCE
        self.THRESHOLD = THRESHOLD

        # derive the paths to the YOLO weights and model configuration
        weightsPath = "yolov33.weights"
        configPath = "yolov3.cfg"

        # load YOLO object detector trained on COCO dataset (80 classes)
        net = cv2.dnn.readNetFromDarknet(configPath, weightsPath)

        # determine only the *output* layer names that we need from YOLO
        ln = net.getLayerNames()
        ln = [ln[i[0] - 1] for i in net.getUnconnectedOutLayers()]

        self.net = net
        self.ln = ln
    
    def forward(self, image):
        """
        feed an image to YOLO network, filter weak boxes, 
        return boxes, confidence, class labels
        """
        (H, W) = image.shape[:2]
        # construct a blob from the input image and then perform a forward
        # pass of the YOLO object detector, giving us our bounding boxes and
        # associated probabilities
        blob = cv2.dnn.blobFromImage(image, 1 / 255.0, (416, 416), swapRB=True, crop=False)
        self.net.setInput(blob)
        start = time.time()
        layerOutputs = self.net.forward(self.ln)
        end = time.time()

        print("[INFO] YOLO took {:.6f} seconds".format(end - start))

        # initialize our lists of detected bounding boxes, confidences, and
        # class IDs, respectively
        boxes = []
        confidences = []
        classIDs = []

        # loop over each of the layer outputs
        for output in layerOutputs:
          # loop over each of the detections
            for detection in output:
                # extract the class ID and confidence
                scores = detection[5:]
                classID = np.argmax(scores)
                confidence = scores[classID]

                # filter out weak predictions 
                if confidence > self.CONFIDENCE:
                    # scale the bounding box coordinates back relative to the
                    # size of the image, keeping in mind that YOLO actually
                    # returns the center (x, y)-coordinates of the bounding
                    # box followed by the boxes' width and height
                    box = detection[0:4] * np.array([W, H, W, H])
                    (centerX, centerY, width, height) = box.astype("int")

                    # use the center (x, y)-coordinates to derive the top and
                    # and left corner of the bounding box
                    x = int(centerX - (width / 2))
                    y = int(centerY + (height / 2))

                    # update our list of bounding box coordinates, confidences,
                    # and class IDs
                    boxes.append([x, y, int(width), int(height)])
                    confidences.append(float(confidence))
                    classIDs.append(classID)

        self.boxes = np.array(boxes)
        self.confidences = np.array(confidences)
        self.classIDs = np.array(classIDs)
    
    def non_max_supression(self):
        """
        perform non-maximum supression over boxes
        """
        idxs = np.argsort(-self.confidences)
        confidences = self.confidences[idxs]
        boxes = self.boxes[idxs]
        classIDs = self.classIDs[idxs]

        for i in range(len(boxes)):
            x,y,w,h = boxes[i][0],  boxes[i][1], boxes[i][2], boxes[i][3]
            box1 = [x, y, x+w, y-h]
            for j in range(i+1, len(boxes)):
                if classIDs[i] == classIDs[j]:

                    # find iou between equal classes
                    x,y,w,h = boxes[j][0], boxes[j][1], boxes[j][2], boxes[j][3]
                    box2 = [x, y, x+w, y-h]
                    if IoU(box1, box2)>self.THRESHOLD:
                        confidences[j] = 0


        idxs = np.where(confidences>0)

        self.boxes = boxes[idxs]
        self.confidences = confidences[idxs]
        self.classIDs = classIDs[idxs]
  
  
    def crop_image(self, a, image):
        return image[max(a[3],0):min(a[1], image.shape[0]),max(a[0],0):min(a[2], image.shape[1]),:]

    def predict(self, image):
        "Find dogs"
        self.forward(image)
        self.non_max_supression()
        rect = []
        for i in range(len(self.boxes)):
            if  self.classIDs[i] > 16 or   self.classIDs[i] < 15:
                continue
           
            # extract the bounding box coordinates
            (x, y) = (self.boxes[i][0], self.boxes[i][1])
            (w, h) = (self.boxes[i][2], self.boxes[i][3])

            rect.append(((x,y),(x+w,y-h)))
        return rect, self.confidences


    def detect(self, image):
        """
        detect objects, supress non maximums, draw boxes
        return image with boxes
        """
        rect, confidence = self.predict(image)
        dogs = []
        for cur_rect in rect:
            # cut part
            cut = self.crop_image((cur_rect[0][0], cur_rect[0][1], cur_rect[1][0], cur_rect[1][1]), image)
            dogs.append(cv2.cvtColor(cut, cv2.COLOR_BGR2RGB))

          # classification
        if len(dogs) == 0:
            return image
        !pip install preprocessing
        from preprocessing import inception_preprocessing
       
        processed_image = inception_preprocessing.preprocess_image(dogs[0], 299, 299, is_training=False)

        img_array = np.array([img_to_array(cv2.resize(img/255, (299,299))) for img in dogs])
        preds = transfer_predict(processed_image)
        print(preds)
        # output = preprocess_input(img_array)
        # preds = my_model.predict(output)

        for i in range(len(preds)):
            #get best pred
            
            m = np.argmax(preds[i])
        
            if preds[i][m] < 0.5:
                label = 'dog '+str(preds[i][m])
            else:

                print(str(m))
                print(data[str(m)])
                label = data[str(m)]+' '+str(preds[i][m])

          # draw a bounding box rectangle and label on the image

            cv2.rectangle(image, rect[i][0], rect[i][1], (255,0,0), 2)
            cv2.putText(image, label, (rect[i][0][0], rect[i][1][1] - 5), cv2.FONT_HERSHEY_SIMPLEX, 0.5, (255,0,0), 2)
        return image


will be placed in the single file you specified.

--2019-11-16 13:53:32--  https://docs.google.com/uc?export=download&id=1WZRUbjLDZRtV6_U6E-yxx8fskuIK3QO5
Resolving docs.google.com (docs.google.com)... 74.125.20.101, 74.125.20.100, 74.125.20.139, ...
Connecting to docs.google.com (docs.google.com)|74.125.20.101|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘yolov3.weights’

yolov3.weights          [ <=>                ]   3.17K  --.-KB/s    in 0s      

2019-11-16 13:53:32 (51.7 MB/s) - ‘yolov3.weights’ saved [3250]

Loading robots.txt; please ignore errors.
--2019-11-16 13:53:32--  https://docs.google.com/robots.txt
Reusing existing connection to docs.google.com:443.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/plain]
Saving to: ‘yolov3.weights’

yolov3.weights          [ <=>                ]     567  --.-KB/s    in 0s      

2019-11-16 13:53:32 (133 MB/s) - ‘yolov3.weights’ saved [567]

--2019-

### TRAIN YOLO


In [0]:
# Generate labels.txt
import csv
with open('dataset/labels.csv', 'r') as fp:
    reader = csv.reader(fp, delimiter=',', quotechar='"')
    next(reader, None)  # skip the headers
    labels = [row[1] for row in reader]
    
sorted_distinct_labels = sorted((set(labels)))
with open('labels.txt', 'w') as f:
  for label in sorted_distinct_labels:
    f.write(label + '\n')



In [0]:
!pip install dicttoxml

  Created wheel for dicttoxml: filename=dicttoxml-1.7.4-cp36-none-any.whl size=17452 sha256=ca81abd984a443579934ef12e33e1d248c37f8cdb03337fb6f7ca8ddf30fe0d3
  Stored in directory: /root/.cache/pip/wheels/62/4f/a3/afd4a68f5add45a668c14efa53b64d5cffb2be6bacf993c151
Successfully built dicttoxml


In [0]:
# SKIP THIS TO GET ALREADY PROCESSED XML_LABELS

path_to_labels = 'dataset/labels.csv'
path_to_dataset = 'dataset/train'

import csv
from dicttoxml import dicttoxml

def generate_xml_annotation(folder='', filename='', width=100, height=100, depth=3, segmented='', name='', pose='Unspecified', truncated=1, difficult=0, xmin=0, ymin=0, xmax=0, ymax=0):
    xml_obj = {
        "annotation": {
            "folder": folder,
            "filename": filename,
            "size": {
                "width": width,
                "height": height,
                "depth": depth
            },
            "segmented": segmented,
            "object": {
                "name": name,
                "pose": pose,
                "truncated": truncated,
                "difficult": difficult,
                "bndbox": {
                    "xmin": xmin,
                    "ymin": ymin,
                    "xmax": xmax,
                    "ymax": ymax
                }
            }
        }
    }
    return dicttoxml(xml_obj, root=False, attr_type=False)
yolo_xml_folder = 'dataset/yolo_xml'
if not os.path.exists(yolo_xml_folder):
  os.mkdir(yolo_xml_folder)

# Read CSV file
with open(path_to_labels, 'r') as fp:
    reader = csv.reader(fp, delimiter=',', quotechar='"')
    next(reader, None)  # skip the headers
    labels = [row for row in reader]

yolo = YOLO()
def process_data_sample(folder, file, label, dest_folder):
    image = cv2.imread(folder + '/' + file + '.jpg')
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    height, width, depth = image.shape
    rects, confidence = yolo.predict(image)
    segmented = 0
    pose = 'Unspecified'
    
    if (len(rects) == 1):
      truncated = 1
      difficult = 0
      rect = rects[0]
      xml_annotation = generate_xml_annotation(folder=folder, filename=file+'.jpg', width=width, height=height, depth=depth, segmented=segmented, name=label, pose=pose, truncated=truncated, difficult=difficult, xmin=rect[0][0], ymin=rect[1][1], xmax=rect[1][0], ymax=rect[0][1])

      with open(dest_folder + '/' + file + '.xml', 'wb') as f:
          f.write(xml_annotation)

for i, label in enumerate(labels):
  print(i, ' from ', len(labels))
  process_data_sample(path_to_dataset, label[0], label[1], yolo_xml_folder)



0  from  10222
[INFO] YOLO took 1.656344 seconds
1  from  10222
[INFO] YOLO took 1.010828 seconds
2  from  10222
[INFO] YOLO took 1.009595 seconds
3  from  10222
[INFO] YOLO took 1.029517 seconds
4  from  10222
[INFO] YOLO took 1.015249 seconds
5  from  10222
[INFO] YOLO took 0.999332 seconds
6  from  10222
[INFO] YOLO took 1.007305 seconds
7  from  10222
[INFO] YOLO took 1.023961 seconds
8  from  10222
[INFO] YOLO took 1.005336 seconds
9  from  10222
[INFO] YOLO took 1.014901 seconds
10  from  10222
[INFO] YOLO took 1.021383 seconds
11  from  10222
[INFO] YOLO took 1.004267 seconds
12  from  10222
[INFO] YOLO took 1.012846 seconds
13  from  10222
[INFO] YOLO took 1.046486 seconds
14  from  10222
[INFO] YOLO took 1.026012 seconds
15  from  10222
[INFO] YOLO took 1.019407 seconds
16  from  10222
[INFO] YOLO took 1.005943 seconds
17  from  10222
[INFO] YOLO took 1.013464 seconds
18  from  10222
[INFO] YOLO took 1.008672 seconds
19  from  10222
[INFO] YOLO took 1.028005 seconds
20  from  

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:16: RuntimeWarning: divide by zero encountered in long_scalars
  app.launch_new_instance()


[INFO] YOLO took 1.019498 seconds
7627  from  10222
[INFO] YOLO took 1.023869 seconds
7628  from  10222
[INFO] YOLO took 1.026024 seconds
7629  from  10222
[INFO] YOLO took 1.089248 seconds
7630  from  10222
[INFO] YOLO took 1.038646 seconds
7631  from  10222
[INFO] YOLO took 1.039527 seconds
7632  from  10222
[INFO] YOLO took 1.047098 seconds
7633  from  10222
[INFO] YOLO took 1.036642 seconds
7634  from  10222
[INFO] YOLO took 1.036328 seconds
7635  from  10222
[INFO] YOLO took 1.042871 seconds
7636  from  10222
[INFO] YOLO took 1.035660 seconds
7637  from  10222
[INFO] YOLO took 1.037719 seconds
7638  from  10222
[INFO] YOLO took 1.065874 seconds
7639  from  10222
[INFO] YOLO took 1.022370 seconds
7640  from  10222
[INFO] YOLO took 1.027926 seconds
7641  from  10222
[INFO] YOLO took 1.043409 seconds
7642  from  10222
[INFO] YOLO took 1.055657 seconds
7643  from  10222
[INFO] YOLO took 1.038871 seconds
7644  from  10222
[INFO] YOLO took 1.032670 seconds
7645  from  10222
[INFO] YOLO 

In [0]:
# SKIP THIS TO GET ALREADY PROCESSED XML_LABELS
!zip -r yolo_dataset.zip dataset/yolo_xml


updating: dataset/yolo_xml/ (stored 0%)
  adding: dataset/yolo_xml/fa3d5cedd5c63e5cc0c04acadf95cb35.xml (deflated 43%)
  adding: dataset/yolo_xml/cac84e1b6d9ca1545dc7f6647b988952.xml (deflated 43%)
  adding: dataset/yolo_xml/24a037230a61e29b7a0e89e8fa27b1b7.xml (deflated 42%)
  adding: dataset/yolo_xml/ac1e8ca8dcdcf845060365dc00631aaf.xml (deflated 42%)
  adding: dataset/yolo_xml/9b370c5ad5420941ed36037665a2ab00.xml (deflated 42%)
  adding: dataset/yolo_xml/f6175a0ef289ef111b225a84240f2e4e.xml (deflated 42%)
  adding: dataset/yolo_xml/b375c3eabf59a3d0e071b8b0343f2d4d.xml (deflated 43%)
  adding: dataset/yolo_xml/273c19effa703469145fa4891d374ac3.xml (deflated 43%)
  adding: dataset/yolo_xml/adfe10ae8d4b90ba0abb56a0648dac8e.xml (deflated 43%)
  adding: dataset/yolo_xml/576b566b73d9cae4190e17d891d51e16.xml (deflated 43%)
  adding: dataset/yolo_xml/73c7d86c561dce0f82e6dec7266bea79.xml (deflated 42%)
  adding: dataset/yolo_xml/3759477c2764d4e01d44d5be03b917f6.xml (deflated 42%)
  adding: da

In [0]:
# GET XML LABELS
!wget --no-check-certificate -r 'https://docs.google.com/uc?export=download&id=1qqPD3FUT24CihD-IAUQ_PEk5yAhHXAzz' -O yolo_xml.zip
!unzip yolo_xml.zip

will be placed in the single file you specified.

--2019-11-16 19:12:26--  https://docs.google.com/uc?export=download&id=1qqPD3FUT24CihD-IAUQ_PEk5yAhHXAzz
Resolving docs.google.com (docs.google.com)... 108.177.97.100, 108.177.97.139, 108.177.97.101, ...
Connecting to docs.google.com (docs.google.com)|108.177.97.100|:443... connected.
HTTP request sent, awaiting response... 302 Moved Temporarily
Location: https://doc-0c-2s-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/1bp6pqq9rp8c3rim1vcvmnmrbuudhe8v/1573927200000/12092491159304354516/*/1qqPD3FUT24CihD-IAUQ_PEk5yAhHXAzz?e=download [following]
--2019-11-16 19:12:46--  https://doc-0c-2s-docs.googleusercontent.com/docs/securesc/ha0ro937gcuc7l7deffksulhg5h7mbp1/1bp6pqq9rp8c3rim1vcvmnmrbuudhe8v/1573927200000/12092491159304354516/*/1qqPD3FUT24CihD-IAUQ_PEk5yAhHXAzz?e=download
Resolving doc-0c-2s-docs.googleusercontent.com (doc-0c-2s-docs.googleusercontent.com)... 74.125.204.132, 2404:6800:4008:c04::84
Connecting to